# Preprocess
<b>Neural Network Architecture</b> The input to the neural network is a 19 × 19 × 17 image stack
comprising 17 binary feature planes. 8 feature planes $X_t$ consist of binary values indicating the
presence of the current player’s stones ($X_t^i = 1$ if intersection $i$ contains a stone of the player’s
colour at time-step $t$; $0$ if the intersection is empty, contains an opponent stone, or if $t < 0$). A
further 8 feature planes, $Y_t$ , represent the corresponding features for the opponent’s stones. The
final feature plane, $C$, represents the colour to play, and has a constant value of either 1 if black
is to play or 0 if white is to play. These planes are concatenated together to give input features
$s_t = [X_t , Y_t , X_{t−1} , Y_{t−1} , ..., X_{t−7} , Y_{t−7} , C]$.

In [1]:
from preprocessing import Preprocess
from go import GameState, BLACK, WHITE, EMPTY
import os, sgf
import numpy as np

# input SGF files
FILE_FOLDER = os.path.join(os.path.expanduser('~'), 'python', 'tutorial_files','go')
# output archive SGF files
SUCCEED_FOLDER = os.path.join(os.path.expanduser('~'), 'python', 'tutorial_files','succeed')
FAIL_FOLDER = os.path.join(os.path.expanduser('~'), 'python', 'tutorial_files','fail')
# output database
TRAIN_DATA = os.path.join(os.path.expanduser('~'), 'python', 'tutorial_data', 'zero', 'train_data')
TEST_DATA = os.path.join(os.path.expanduser('~'), 'python', 'tutorial_data', 'zero', 'test_data')

# Config this to indicate whether it's training or testing data
DATA_FOLDER = TEST_DATA


# BOARD_POSITION contains SGF symbol which represents each row (or column) of the board
# It can be used to convert between 0,1,2,3... and a,b,c,d...
# Symbol [tt] or [] represents PASS in SGF, therefore is omitted
BOARD_POSITION = 'abcdefghijklmnopqrs'

DEFAULT_FEATURES = ["board", "color"]

## Define DB output
  [LevelDB](http://leveldb.org/) is preferred database because it automatically use [Snappy](https://github.com/google/snappy) to compress the data.

In [2]:
from caffe2.python import core, utils
from caffe2.proto import caffe2_pb2

def write_db(db_type, db_name, base_name, features, labels):
    db = core.C.create_db(db_type, db_name, core.C.Mode.write)
    transaction = db.new_transaction()
    for i in range(features.shape[0]):
        feature_and_label = caffe2_pb2.TensorProtos()
        feature_and_label.protos.extend([
             utils.NumpyArrayToCaffe2Tensor(features[i]),
             utils.NumpyArrayToCaffe2Tensor(labels[i])
        ])
        transaction.put(
            '{}_{:0=3}'.format(base_name,i),
            feature_and_label.SerializeToString())
    # Close the transaction, and then close the db.
    del transaction
    del db

## Parse SGF game file
  Parse the SGF file. SGF file use characters a to s to represents line 1 to 19. We convert SGF to Caffe2 Tensor. And write back database in batch of game.

In [3]:
#%%capture output
p = Preprocess(DEFAULT_FEATURES)
for dirname, subDirList, fileList in os.walk(FILE_FOLDER):
    for filename in fileList:
        with open(os.path.join(dirname, filename)) as f:
            collection = sgf.parse(f.read())
            for game in collection:
                if game.nodes[0].properties['SZ'] == ['19']: # Size of the Board should only be 19x19
                    state = GameState() # Initialize GameState
                    features = np.empty(shape=(0,17,19,19), dtype=np.int8)
                    labels = np.empty(shape=(0,1), dtype=np.uint16)
                    try:
                        for node in game.nodes[1:]: # Except nodes[0] for game properties
                            features = np.append(features, p.state_to_tensor(state).astype(np.int8), axis=0)
                            if 'B' in node.properties and len(node.properties['B'][0]) == 2: # Black move
                                x = BOARD_POSITION.index(node.properties['B'][0][0])
                                y = BOARD_POSITION.index(node.properties['B'][0][1])
                                state.do_move(action=(x,y),color = BLACK)
                            elif 'W' in node.properties and len(node.properties['W'][0]) == 2: # White move
                                x = BOARD_POSITION.index(node.properties['W'][0][0])
                                y = BOARD_POSITION.index(node.properties['W'][0][1])
                                state.do_move(action=(x,y),color = WHITE)
                            labels = np.append(labels, np.asarray([[x * 19 + y]], dtype=np.uint16), axis=0)
                        write_db(
                            db_type = 'leveldb',
                            db_name = DATA_FOLDER, # replace this with TRAIN_DATA or TEST_DATA if you want to separate the dataset
                            base_name = os.path.basename(filename),
                            features = features,
                            labels = labels
                        )
                        os.rename(f.name,os.path.join(SUCCEED_FOLDER,filename)) # move the file to SUCCEED_FOLDER, so Preprocess can resume after interrupted
                        print('{} succeeded'.format(filename))
                    except Exception as e:
                        os.rename(f.name,os.path.join(FAIL_FOLDER,filename)) # move the file to FAIL_FOLDER, so Preprocess can resume after interrupted
                        print('{} failed dues to {}'.format(filename, e))

2006-05-17-20.sgf succeeded
2006-01-01-1.sgf succeeded
2006-01-01-10.sgf failed dues to (15, 7)
2006-01-01-11.sgf succeeded
2006-01-01-12.sgf succeeded
2006-01-01-13.sgf succeeded
2006-01-01-14.sgf failed dues to (16, 4)
2006-01-01-15.sgf succeeded
2006-01-01-16.sgf succeeded
2006-01-01-17.sgf succeeded
2006-01-01-18.sgf succeeded
2006-01-01-19.sgf succeeded
2006-01-01-2.sgf succeeded
2006-01-01-20.sgf succeeded
2006-01-01-21.sgf succeeded
2006-01-01-22.sgf succeeded
2006-01-01-23.sgf succeeded
2006-01-01-25.sgf failed dues to (15, 1)
2006-01-01-26.sgf succeeded
2006-01-01-27.sgf succeeded
2006-01-01-28.sgf succeeded
2006-01-01-29.sgf succeeded
2006-01-01-3.sgf succeeded
2006-01-01-30.sgf succeeded
2006-01-01-31.sgf failed dues to (0, 7)
2006-01-01-32.sgf succeeded
2006-01-01-33.sgf succeeded
2006-01-01-34.sgf succeeded
2006-01-01-4.sgf succeeded
2006-01-01-5.sgf succeeded
2006-01-01-6.sgf succeeded
2006-01-01-7.sgf succeeded
2006-01-01-8.sgf succeeded
2006-01-02-1.sgf succeeded
2006-0

2006-01-09-6.sgf succeeded
2006-01-09-7.sgf succeeded
2006-01-09-8.sgf succeeded
2006-01-09-9.sgf succeeded
2006-01-10-1.sgf succeeded
2006-01-10-10.sgf succeeded
2006-01-10-11.sgf succeeded
2006-01-10-12.sgf succeeded
2006-01-10-13.sgf succeeded
2006-01-10-14.sgf succeeded
2006-01-10-15.sgf succeeded
2006-01-10-16.sgf succeeded
2006-01-10-17.sgf succeeded
2006-01-10-18.sgf succeeded
2006-01-10-19.sgf succeeded
2006-01-10-20.sgf succeeded
2006-01-10-21.sgf succeeded
2006-01-10-22.sgf succeeded
2006-01-10-23.sgf succeeded
2006-01-10-24.sgf succeeded
2006-01-10-25.sgf failed dues to (15, 4)
2006-01-10-3.sgf succeeded
2006-01-10-4.sgf succeeded
2006-01-10-5.sgf succeeded
2006-01-10-6.sgf succeeded
2006-01-10-7.sgf succeeded
2006-01-10-8.sgf succeeded
2006-01-10-9.sgf failed dues to (5, 14)
2006-01-11-1.sgf succeeded
2006-01-11-10.sgf succeeded
2006-01-11-11.sgf succeeded
2006-01-11-13.sgf succeeded
2006-01-11-14.sgf succeeded
2006-01-11-15.sgf succeeded
2006-01-11-16.sgf succeeded
2006-01

2006-01-21-23.sgf succeeded
2006-01-21-24.sgf failed dues to (2, 14)
2006-01-21-25.sgf succeeded
2006-01-21-26.sgf succeeded
2006-01-21-27.sgf succeeded
2006-01-21-28.sgf succeeded
2006-01-21-29.sgf succeeded
2006-01-21-3.sgf succeeded
2006-01-21-30.sgf succeeded
2006-01-21-32.sgf succeeded
2006-01-21-33.sgf succeeded
2006-01-21-34.sgf succeeded
2006-01-21-35.sgf succeeded
2006-01-21-4.sgf succeeded
2006-01-21-5.sgf succeeded
2006-01-21-6.sgf succeeded
2006-01-21-7.sgf succeeded
2006-01-21-8.sgf succeeded
2006-01-21-9.sgf succeeded
2006-01-22-1.sgf succeeded
2006-01-22-10.sgf succeeded
2006-01-22-11.sgf succeeded
2006-01-22-12.sgf succeeded
2006-01-22-13.sgf succeeded
2006-01-22-14.sgf succeeded
2006-01-22-16.sgf succeeded
2006-01-22-17.sgf succeeded
2006-01-22-18.sgf succeeded
2006-01-22-19.sgf succeeded
2006-01-22-2.sgf succeeded
2006-01-22-20.sgf succeeded
2006-01-22-21.sgf succeeded
2006-01-22-22.sgf succeeded
2006-01-22-23.sgf succeeded
2006-01-22-24.sgf succeeded
2006-01-22-25.sg

2006-01-29-4.sgf succeeded
2006-01-29-40.sgf succeeded
2006-01-29-41.sgf succeeded
2006-01-29-42.sgf succeeded
2006-01-29-5.sgf succeeded
2006-01-29-6.sgf succeeded
2006-01-29-7.sgf succeeded
2006-01-29-8.sgf succeeded
2006-01-30-1.sgf succeeded
2006-01-30-10.sgf succeeded
2006-01-30-11.sgf succeeded
2006-01-30-12.sgf succeeded
2006-01-30-13.sgf succeeded
2006-01-30-14.sgf succeeded
2006-01-30-15.sgf succeeded
2006-01-30-16.sgf succeeded
2006-01-30-2.sgf succeeded
2006-01-30-3.sgf succeeded
2006-01-30-4.sgf succeeded
2006-01-30-5.sgf succeeded
2006-01-30-6.sgf succeeded
2006-01-30-7.sgf succeeded
2006-01-30-8.sgf succeeded
2006-01-30-9.sgf succeeded
2006-01-31-10.sgf succeeded
2006-01-31-11.sgf succeeded
2006-01-31-12.sgf succeeded
2006-01-31-13.sgf succeeded
2006-01-31-14.sgf succeeded
2006-01-31-15.sgf succeeded
2006-01-31-16.sgf succeeded
2006-01-31-17.sgf succeeded
2006-01-31-18.sgf succeeded
2006-01-31-2.sgf succeeded
2006-01-31-3.sgf succeeded
2006-01-31-4.sgf succeeded
2006-01-3

2006-02-10-11.sgf succeeded
2006-02-10-12.sgf succeeded
2006-02-10-14.sgf succeeded
2006-02-10-15.sgf succeeded
2006-02-10-16.sgf succeeded
2006-02-10-17.sgf succeeded
2006-02-10-18.sgf succeeded
2006-02-10-19.sgf succeeded
2006-02-10-2.sgf failed dues to (17, 3)
2006-02-10-20.sgf succeeded
2006-02-10-21.sgf failed dues to (2, 16)
2006-02-10-22.sgf succeeded
2006-02-10-23.sgf succeeded
2006-02-10-24.sgf succeeded
2006-02-10-3.sgf succeeded
2006-02-10-4.sgf succeeded
2006-02-10-5.sgf succeeded
2006-02-10-6.sgf succeeded
2006-02-10-8.sgf succeeded
2006-02-10-9.sgf succeeded
2006-02-11-1.sgf succeeded
2006-02-11-10.sgf succeeded
2006-02-11-11.sgf succeeded
2006-02-11-12.sgf succeeded
2006-02-11-13.sgf succeeded
2006-02-11-14.sgf failed dues to (2, 14)
2006-02-11-15.sgf succeeded
2006-02-11-16.sgf succeeded
2006-02-11-17.sgf succeeded
2006-02-11-18.sgf succeeded
2006-02-11-19.sgf succeeded
2006-02-11-2.sgf succeeded
2006-02-11-20.sgf succeeded
2006-02-11-21.sgf succeeded
2006-02-11-23.sgf 

...

2005-11-29-15.sgf succeeded
2005-11-29-16.sgf failed dues to (0, 4)
2005-11-29-17.sgf succeeded
2005-11-29-18.sgf succeeded
2005-11-29-19.sgf succeeded
2005-11-29-2.sgf succeeded
2005-11-29-21.sgf failed dues to (14, 3)
2005-11-29-22.sgf succeeded
2005-11-29-23.sgf succeeded
2005-11-29-24.sgf succeeded
2005-11-29-25.sgf succeeded
2005-11-29-26.sgf succeeded
2005-11-29-27.sgf succeeded
2005-11-29-3.sgf succeeded
2005-11-29-4.sgf succeeded
2005-11-29-5.sgf succeeded
2005-11-29-6.sgf succeeded
2005-11-29-7.sgf failed dues to (3, 16)
2005-11-29-8.sgf failed dues to (16, 4)
2005-11-29-9.sgf succeeded
2005-11-30-1.sgf succeeded
2005-11-30-10.sgf succeeded
2005-11-30-12.sgf succeeded
2005-11-30-13.sgf succeeded
2005-11-30-14.sgf succeeded
2005-11-30-15.sgf succeeded
2005-11-30-16.sgf succeeded
2005-11-30-17.sgf succeeded
2005-11-30-18.sgf succeeded
2005-11-30-19.sgf succeeded
2005-11-30-2.sgf succeeded
2005-11-30-20.sgf failed dues to (6, 4)
2005-11-30-21.sgf succeeded
2005-11-30-22.sgf succe

2005-12-06-27.sgf succeeded
2005-12-06-28.sgf succeeded
2005-12-06-29.sgf succeeded
2005-12-06-3.sgf succeeded
2005-12-06-30.sgf succeeded
2005-12-06-31.sgf succeeded
2005-12-06-32.sgf succeeded
2005-12-06-34.sgf succeeded
2005-12-06-35.sgf succeeded
2005-12-06-36.sgf succeeded
2005-12-06-37.sgf succeeded
2005-12-06-38.sgf succeeded
2005-12-06-39.sgf succeeded
2005-12-06-4.sgf succeeded
2005-12-06-5.sgf succeeded
2005-12-06-6.sgf succeeded
2005-12-06-7.sgf succeeded
2005-12-06-8.sgf succeeded
2005-12-06-9.sgf succeeded
2005-12-07-1.sgf succeeded
2005-12-07-10.sgf succeeded
2005-12-07-11.sgf failed dues to (15, 4)
2005-12-07-12.sgf succeeded
2005-12-07-14.sgf succeeded
2005-12-07-15.sgf succeeded
2005-12-07-16.sgf succeeded
2005-12-07-17.sgf succeeded
2005-12-07-18.sgf succeeded
2005-12-07-19.sgf succeeded
2005-12-07-2.sgf succeeded
2005-12-07-20.sgf failed dues to (9, 9)
2005-12-07-21.sgf succeeded
2005-12-07-22.sgf succeeded
2005-12-07-23.sgf succeeded
2005-12-07-24.sgf succeeded
2005

2005-12-11-30.sgf succeeded
2005-12-11-31.sgf succeeded
2005-12-11-32.sgf succeeded
2005-12-11-33.sgf succeeded
2005-12-11-34.sgf succeeded
2005-12-11-35.sgf succeeded
2005-12-11-36.sgf succeeded
2005-12-11-37.sgf succeeded
2005-12-11-39.sgf succeeded
2005-12-11-4.sgf succeeded
2005-12-11-40.sgf succeeded
2005-12-11-41.sgf succeeded
2005-12-11-42.sgf succeeded
2005-12-11-43.sgf succeeded
2005-12-11-44.sgf succeeded
2005-12-11-45.sgf succeeded
2005-12-11-46.sgf succeeded
2005-12-11-47.sgf succeeded
2005-12-11-48.sgf succeeded
2005-12-11-49.sgf succeeded
2005-12-11-5.sgf succeeded
2005-12-11-50.sgf succeeded
2005-12-11-51.sgf succeeded
2005-12-11-52.sgf succeeded
2005-12-11-54.sgf succeeded
2005-12-11-55.sgf succeeded
2005-12-11-56.sgf succeeded
2005-12-11-57.sgf succeeded
2005-12-11-58.sgf succeeded
2005-12-11-59.sgf succeeded
2005-12-11-6.sgf succeeded
2005-12-11-60.sgf succeeded
2005-12-11-61.sgf succeeded
2005-12-11-62.sgf succeeded
2005-12-11-63.sgf succeeded
2005-12-11-64.sgf succe

2005-12-18-24.sgf succeeded
2005-12-18-25.sgf succeeded
2005-12-18-26.sgf succeeded
2005-12-18-27.sgf succeeded
2005-12-18-28.sgf succeeded
2005-12-18-29.sgf succeeded
2005-12-18-30.sgf succeeded
2005-12-18-31.sgf succeeded
2005-12-18-32.sgf succeeded
2005-12-18-33.sgf succeeded
2005-12-18-34.sgf succeeded
2005-12-18-35.sgf succeeded
2005-12-18-36.sgf succeeded
2005-12-18-37.sgf succeeded
2005-12-18-38.sgf succeeded
2005-12-18-39.sgf succeeded
2005-12-18-4.sgf succeeded
2005-12-18-40.sgf succeeded
2005-12-18-41.sgf succeeded
2005-12-18-42.sgf succeeded
2005-12-18-43.sgf succeeded
2005-12-18-44.sgf succeeded
2005-12-18-46.sgf succeeded
2005-12-18-47.sgf succeeded
2005-12-18-48.sgf succeeded
2005-12-18-49.sgf succeeded
2005-12-18-5.sgf succeeded
2005-12-18-50.sgf succeeded
2005-12-18-51.sgf failed dues to (9, 3)
2005-12-18-52.sgf failed dues to (3, 10)
2005-12-18-53.sgf succeeded
2005-12-18-54.sgf succeeded
2005-12-18-55.sgf succeeded
2005-12-18-56.sgf succeeded
2005-12-18-6.sgf succeede

2005-12-24-8.sgf succeeded
2005-12-24-9.sgf succeeded
2005-12-25-1.sgf succeeded
2005-12-25-10.sgf succeeded
2005-12-25-12.sgf succeeded
2005-12-25-13.sgf failed dues to (16, 2)
2005-12-25-14.sgf succeeded
2005-12-25-15.sgf succeeded
2005-12-25-16.sgf succeeded
2005-12-25-17.sgf succeeded
2005-12-25-18.sgf succeeded
2005-12-25-19.sgf succeeded
2005-12-25-2.sgf succeeded
2005-12-25-20.sgf succeeded
2005-12-25-21.sgf succeeded
2005-12-25-22.sgf succeeded
2005-12-25-23.sgf succeeded
2005-12-25-24.sgf succeeded
2005-12-25-25.sgf succeeded
2005-12-25-26.sgf succeeded
2005-12-25-28.sgf succeeded
2005-12-25-29.sgf failed dues to (3, 13)
2005-12-25-3.sgf succeeded
2005-12-25-30.sgf succeeded
2005-12-25-31.sgf succeeded
2005-12-25-32.sgf succeeded
2005-12-25-33.sgf succeeded
2005-12-25-34.sgf succeeded
2005-12-25-35.sgf succeeded
2005-12-25-36.sgf succeeded
2005-12-25-37.sgf succeeded
2005-12-25-38.sgf succeeded
2005-12-25-39.sgf succeeded
2005-12-25-4.sgf succeeded
2005-12-25-40.sgf succeeded
